<a href="https://colab.research.google.com/github/anon560096/bds_project/blob/master/code/yelp_dataset_prediction.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [0]:
%reload_ext autoreload
%autoreload 2
%matplotlib inline

In [0]:
from fastai import *
from fastai.vision import *
from fastai.callbacks import *
from shutil import copyfile
from sklearn.manifold import TSNE
import seaborn as sns
from sklearn import manifold, datasets
from sklearn.metrics.pairwise import pairwise_distances
from sklearn.metrics import confusion_matrix
from scipy.spatial.distance import squareform
from matplotlib.offsetbox import OffsetImage, AnnotationBbox
from matplotlib.ticker import NullFormatter
import PIL

Kaggle API installation and dataset download

In [0]:
from google.colab import files

# Install Kaggle library
!pip install -q kaggle

In [0]:
uploaded = files.upload()

Saving kaggle.json to kaggle.json


In [0]:
!mkdir -p ~/.kaggle
!cp kaggle.json ~/.kaggle/

In [0]:
!kaggle competitions download -c yelp-restaurant-photo-classification

  0% 0.00/1.12M [00:00<?, ?B/s]
100% 1.12M/1.12M [00:00<00:00, 74.1MB/s]
  0% 0.00/7.12k [00:00<?, ?B/s]
100% 7.12k/7.12k [00:00<00:00, 7.08MB/s]
100% 6.54G/6.54G [03:14<00:00, 52.4MB/s]
100% 6.54G/6.54G [03:14<00:00, 36.1MB/s]
100% 6.60G/6.61G [04:01<00:00, 42.6MB/s]
100% 6.61G/6.61G [04:01<00:00, 29.4MB/s]
  0% 0.00/39.0k [00:00<?, ?B/s]
100% 39.0k/39.0k [00:00<00:00, 41.4MB/s]
100% 4.79M/4.79M [00:00<00:00, 44.8MB/s]



In [0]:
print("Extracting training data..")
!tar -xvf 'train_photos.tgz' > filenames.txt
print("Extraction done!")

print("Removing tar file...")
!rm train_photos.tgz

Extracting training data..
tar: train_photos/312453.jpg: Wrote only 8192 of 9216 bytes
tar: train_photos/._312455.jpg: Cannot write: No space left on device
tar: train_photos/312455.jpg: Cannot write: No space left on device
tar: train_photos/._312459.jpg: Cannot write: No space left on device
tar: train_photos/312459.jpg: Cannot write: No space left on device
tar: train_photos/._312460.jpg: Cannot write: No space left on device
tar: train_photos/312460.jpg: Cannot write: No space left on device
tar: train_photos/._312462.jpg: Cannot write: No space left on device
tar: train_photos/312462.jpg: Cannot write: No space left on device
tar: train_photos/._312464.jpg: Cannot write: No space left on device
tar: train_photos/312464.jpg: Cannot write: No space left on device
tar: train_photos/._312465.jpg: Cannot write: No space left on device
tar: train_photos/312465.jpg: Cannot write: No space left on device
tar: train_photos/._312468.jpg: Cannot write: No space left on device
tar: train_phot

In [0]:
path = Path('')
Path.mkdir(path/'data', exist_ok=True)

# path = path/'data'
learnt_model = load_learner(path/'data/models')

In [0]:
tfms = get_transforms(
                        do_flip=True,
                        flip_vert=True,
                        max_rotate=10.0,
                        max_zoom = 1.1,
                        max_lighting=0.25,
                        max_warp=0.25,
                        )

In [0]:
data = (ImageList.from_folder(path/'data').split_by_folder(train='train', valid='test')
                                       .label_from_folder()
                                       .transform(tfms=tfms, size=512)
                                       .databunch(bs=1, num_workers=1))
# path
# data_test = ImageList.from_folder(path/'data').split_by_folder(train='train', valid='test').label_from_folder().transform(tfms=tfms, size=512).databunch(bs=1, num_workers=1)

# data_test = (ImageList.from_folder(path/'data/test').split_by_folder(train='train', valid='test')
#                                         .label_from_folder(classes=None)
#                                        .transform(tfms=tfms, size=512)
#                                        .databunch(bs=128, num_workers=1))

/usr/local/lib/python3.6/dist-packages/fastai/data_block.py:537: UserWarning: You are labelling your items with CategoryList.
Your valid set contained the following unknown labels, the corresponding items have been discarded.
test
  if getattr(ds, 'warn', False): warn(ds.warn)


In [0]:
learn = cnn_learner(data, models.resnet50, metrics=error_rate)
# apply mixup
learn = learn.mixup()

Downloading: "https://download.pytorch.org/models/resnet50-19c8e357.pth" to /root/.cache/torch/checkpoints/resnet50-19c8e357.pth
100%|██████████| 97.8M/97.8M [00:02<00:00, 42.9MB/s]


In [0]:
# learn.load('food_mix_aug_nls-3')
learn = load_learner('data/models/food_mix_aug_nls-3')

FileNotFoundError: ignored

In [0]:
# data_test = (ImageList.from_folder(path/'data').split_by_folder(train='train', valid='test')
#                                        .label_from_folder(classes=None)
#                                        .transform(tfms=tfms, size=512)
#                                        .databunch(bs=128, num_workers=1))
# data.valid_ds

# split_by_folder(train='train', valid='test')
learnt_model = learnt_model.to_fp32()
img = open_image('data/train/img2.jpeg')
pred = learnt_model.predict(img)
pred

(Category tacos,
 tensor(96),
 tensor([2.6664e-04, 7.0906e-04, 7.0601e-03, 8.6105e-03, 8.7719e-04, 3.4602e-03,
         2.0445e-03, 3.6634e-03, 1.1763e-04, 8.3074e-04, 2.3027e-02, 6.4399e-02,
         6.9373e-04, 2.9551e-03, 7.2517e-04, 1.6707e-02, 1.7236e-04, 1.4436e-04,
         4.6930e-03, 2.6017e-03, 3.0560e-03, 2.8763e-03, 1.1522e-03, 4.4068e-03,
         1.3036e-02, 8.5748e-03, 1.8822e-03, 4.0709e-04, 5.2613e-04, 1.2598e-03,
         8.5904e-03, 4.8742e-03, 9.2884e-03, 3.6836e-03, 7.9235e-04, 1.5908e-02,
         1.1507e-02, 3.3313e-04, 7.7197e-03, 8.4855e-04, 6.9552e-02, 1.9814e-03,
         1.4118e-04, 3.8671e-03, 5.0097e-03, 1.5625e-03, 1.4193e-02, 3.1052e-02,
         1.5671e-03, 1.8359e-03, 9.2451e-04, 2.3333e-03, 1.4033e-03, 1.1126e-03,
         2.5813e-02, 5.0960e-04, 7.8450e-04, 3.0339e-03, 1.8868e-03, 1.1044e-03,
         5.2260e-03, 1.0045e-02, 1.6064e-03, 7.8216e-04, 2.5982e-03, 9.7613e-02,
         1.5743e-02, 2.5623e-04, 3.7428e-03, 5.1498e-04, 1.4317e-02, 8.2368e-02